In [29]:
import numpy as np
import pandas as pd
from IPython.core.display import HTML

def pretty(dataframe):
    display(dataframe.style.format({'funding': '{:,} €'}))

raw_data = pd.read_csv('1.C.1.csv', delimiter=';')
data = raw_data[raw_data.year == 2018].drop('year', 1)

unis = dict()
for uni in data.university.unique():
    unis[uni] = list()
    uni_data = data[data.university == uni].funding.sum()
    #if not uni.startswith("Univ") or uni_data < 5000000:
    #    data = data[data.university != uni]
 
table = pd.pivot_table(data, values='funding', index=['university'],
                       columns=['funder'], fill_value=0, #margins=True,
                       aggfunc=np.sum)

totals_abs = table.sum()
totals_avg = table.mean()
totals = totals_abs/totals_abs.sum()

sums = table.agg(['sum'], axis="columns")['sum']
sums_avg = table.agg(['mean'], axis="columns")['mean']

interesting = 1 * table.gt(sums_avg, axis="rows") \
            + 2 * table.div(sums, axis="rows").gt(totals) \
            + 4 * table.gt(totals_avg, axis="columns") 


#1: uniintern
#2: vergleichend, relativ
#3: systemisch

interesting = interesting.rename(index=str, columns={'sonstige': 'sonstige Fördergeber', 'nicht bekannt / nicht zuordenbar': 'nicht zuordenbare Fördergeber'})
headers = interesting.columns
for row in interesting.itertuples():
    (uni, *values) = row
    for idx, element in enumerate(values):
        funder = headers[idx]
        switcher = [
            '',
            '$funder ist zwar uniintern wichtig, aber andere Universitäten setzen stärker auf $funder. Für $funder ist die Universität nicht relevant.',
            'Die $uni ist von $funder stärker abhängig als andere Universitäten, auch wenn $funder uniintern keine hohe Bedeutung hat. Auch für $funder ist die Universität nicht relevant.',
            '$funder ist sowohl innerhalb der Universität als auch im relativen Vergleich mit anderen eine wichtige Geldquelle. Für $funder allerdings ist die $uni nicht relevant.',
            'Für $funder ist die Universität bedeutsam, aber innerhalb und im relativen Vergleich mit anderen Universitäten ist $funder nicht relevant.',
            'Obwohl die Universität bei $funder eine erfolgreiche Fördernehmerin ist, konzentrieren andere Universitäten stärker auf $funder. Dennoch ist $funder einer der großen Förderer .',
            'Die Universität ist erfolgreich bei $funder und auch für $funder ist die $uni relevant. Nur uniintern hat $funder keine große Bedeutung.',
            '$funder ist ein wichtiger Fördergeber, sowohl intern als auch im relativen Vergleich mit anderen Universitäten. Und auch für $funder ist die $uni eine wichtige Partnerin.'           
        ]
        
        text = switcher[element].replace('$uni', uni).replace('$funder', '<strong>' + funder + '</strong>')
        if text != '':
            text = text[0:1].capitalize() + text[1:]
            unis[uni].append((element, text, funder))
            
for uni, statements in unis.items():
    if len(statements) > 0:
        statements.sort(key=lambda tup: tup[0], reverse=True)
        old_importance = 0
        display(HTML('<h3>' + uni + '</h3><p style="font-family:verdana">'))
        text = ''
        for statement in statements:
            importance = statement[0]
            if importance == old_importance:
                text += 'Dies lässt sich ebenso über <strong>' + statement[2] + '</strong> sagen.'
            else:
                text += '<br/>' + statement[1]
            text += ' '
            old_importance = importance
            
        display(HTML(text + '</p>'))
        
        
table['Summe'] = table.agg(['sum'], axis="columns")

display(table.style.format('{:,} €'))
    
print('{:,} €'.format(table.loc[('Universität Wien', 'Summe')]))

74,550,657 €


In [69]:

class Dimension:
    @classmethod
    def create(cls, dataframe, dimensions):
        dims = list()
        for dim in dimensions:
            assert dim in dataframe, "There is no column '" + dim + "'"
            cats = dataframe[dim].unique()
            dims.append(Dimension(dim, cats))
        return dims
        
    def __init__(self, name, categories):
        self.__name = name
        self.__categories = categories
        
class Analysis:
    def __init__(self, datasheet, description, about, dataframe):
        self.__sheet = datasheet
        self.__data = pd.pivot_table(dataframe, fill_value=0, aggfunc=np.sum,
                                     values=datasheet.value_column_name,
                                     index=[datasheet.university_column_name],
                                     columns=about)
        if isinstance(about, list):
            self.__about = about
        else:
            self.__about = [about]
        self.__description = description
        self.__columns_total = self.__data.agg(['sum'], axis='columns')['sum']
        self.__rows_total = self.__data.agg(['sum'], axis='rows')
        self.__universities = dataframe[datasheet.university_column_name].unique()
        
    horizontal = "rows"
    vertical = "columns"
        
    @property
    def table(self):
        return self.__data
    @property
    def description(self):
        return self.__description
    @property
    def datasheet(self):
        return self.__sheet  
    @property
    def about(self):
        return self.__about
    @property
    def horizontal_total(self):
        return self.__columns_total
    @property
    def vertical_total(self):
        return self.__rows_total    
    @property
    def universities(self):
        return self.__universities
        
class Ranking:
    def __init__(self, analysis):
        self.__analysis = analysis
        self.__ranking = analysis.horizontal_total.div(analysis.horizontal_total.sum()). \
                            sort_values(ascending=False).reset_index()
        self.__ranking = self.__ranking.rename(index=int, columns={'sum': 'value'})
        self.__ranking.index += 1
    
    @property
    def ranking(self):
        return self.__ranking
    
    def rank_of(self, university):
        assert university in self.__analysis.universities, university + " is not included in this analysis"
        ranking = self.ranking
        idx = ranking.loc[ranking['index'] == university].index
        assert len(idx) == 1
        return int(idx[0])
    
    def better_rank_than(self, university):
        rank = int(self.rank_of(university))
        return self.top(rank-1)
    
    def top(self, rank):
        ranking = self.ranking
        return ranking.loc[ranking.index <= rank]        
        
        
class Structure:
    def __init__(self, analysis):
        self.__analysis = analysis
        #self.__avg = analysis.dataframe.agg(['mean'], axis='columns')['mean']
        self.__structure = analysis.table.div(analysis.horizontal_total, axis=Analysis.horizontal)
        self.__total_structure = analysis.vertical_total.div(analysis.vertical_total.iloc[0].sum())      
        self.__reverse_structure = analysis.table.div(analysis.vertical_total.iloc[0])
        self.__reverse_total_structure = analysis.horizontal_total.div(analysis.horizontal_total.sum()). \
                                            sort_values(ascending=False).reset_index()
        self.__reverse_total_structure.index += 1       
        self.__similarity_matrix = Similarity(analysis, self.__structure)
        #display(self.__structure.style.format('{0:.1%}'))
        #display(self.__reverse_structure.style.format('{0:.1%}'))
        #display(self.__total_structure.style.format('{0:.1%}'))        
        #print(self.__reverse_total_structure)
        
    @property
    def total(self):
        assert self.__analysis.horizontal_total.sum() == self.__analysis.vertical_total.iloc[0].sum()
        return self.__analysis.horizontal_total.sum()
    @property
    def table(self):
        return self.__structure
    @property
    def similarities(self):
        return self.__similarity_matrix
    
    def structure_of(self, university):
        assert university in self.__analysis.universities, university + " is not included in this analysis"
        tmp = self.__structure.loc[university].sort_values(ascending=False).reset_index()
        tmp.index += 1
        return tmp

class Datasheet:
    def __init__(self, dataframe, dimensions, timepoint_name, university_name, value_name):
        assert timepoint_name in dataframe, "There is no column '" + timepoint_name + "'"
        assert university_name in dataframe, "There is no column '" + university_name + "'"
        assert value_name in dataframe, "There is no colum with valid data called '" + value_name + "'"
        self.__dataframe = dataframe
        self.__timepoint_column = timepoint_name
        self.__university_column = university_name
        self.__value_column = value_name       
        self.__dimensions = Dimension.create(dataframe, dimensions)
        self.__timepoints = dataframe[timepoint_name].unique()
        self.__universities = dataframe[university_name].unique()
        self.__current_timepoint = dataframe[timepoint_name].max()
        
    @property
    def value_column_name(self):
        return self.__value_column
    @property
    def university_column_name(self):
        return self.__university_column
    @property
    def most_recent(self):
        return self.__current_timepoint
    
    def only(self, conditions):
        df = self.__dataframe
        for cond_column, cond_filter in conditions.items():
            if isinstance(cond_filter, list):
                df = df[df[cond_column].isin(cond_filter)]
            else:
                df = df[df[cond_column] == cond_filter]
        return df
    
    def analyze(self, description, about, filtering):
        return Analysis(self, description, about, self.only(filtering))        
              
        
            
class Similarity:
    def __init__(self, analysis, table):
        self.__table = table
        self.__analysis = analysis
        self.__matrix = self.__create_matrix(analysis)
        self.__distances = self.__create_distances()
        self.__num_categories = len(analysis.table.columns)
        self.__max_distance = len(analysis.table.columns)**(1/2)
        
        print("Ähnlichkeitsmatrix:")
        display(self.__matrix)

    def __create_distances(self):
        upper_triangle = np.triu(np.ones(self.__matrix.shape), 1).astype(np.bool)
        return self.matrix.where(upper_triangle).stack().reset_index()        
        
    def __create_matrix(self, analysis):
        unis = analysis.universities
        distances = pd.DataFrame(columns=['base', 'university', 'distance'])
        for uni in analysis.universities:
            dist = pd.DataFrame(columns=['base', 'university', 'distance'])       
            dist[['university', 'distance']] = self.__to(uni)
            dist[['base']] = uni
            distances = pd.merge(distances, dist, how='outer')
        return distances.set_index(['base', 'university']).unstack()
        
    @property
    def matrix(self):
        return self.__matrix
        
    def __to(self, university):
        tbl = self.__table
        base_row = tbl.loc[university]
        
        base_row_filter = base_row > 0
        maximum_similarity = base_row_filter.sum()
        
        tmp = tbl.mul(1*base_row_filter)
        print("TMP for " + university +":")
        display(tmp)
        
        sim = tmp.div(base_row)
        display(sim)
        
        dists = tbl.sub(base_row).abs().sum(Analysis.vertical).reset_index()
        dists.columns = ['university', 'distance']
        dists = dists.replace([np.inf, -np.inf], np.nan)
        
        #print("Dists for" + university + ":")
        #display(dists)
        
        #dists = ((tbl.sub(base_row)**2).sum(Analysis.vertical)**(1/2)).reset_index()
        return dists
    
    def to(self, university):
        m = self.matrix
        return m.loc[university].sort_values()[1:]
    
    def most_similar_to(self, university, quantile=0.2):
        m = self.matrix
        q = self.__distances.distance.quantile(quantile)
        
        s = m.loc[university]
        s = s[s < q].sort_values().reset_index().drop(columns='level_0')[1:]
        s[university] = 1 - (s[university] / self.__max_distance)
        s.columns = ['university', 'similarity']
        return s
        
    
    
        
funding = Datasheet(raw_data, ['funder', 'fos'], 'year', 'university', 'funding')

analysis = funding.analyze('Drittmittelanalyse', 'funder', {'year': funding.most_recent})
uni = "Universität Wien"

s = Structure(analysis)
r = Ranking(analysis)

    
analysis2 = funding.analyze('Forschungsprofil', 'fos', {'year': funding.most_recent})
s2 = Structure(analysis2)

display(s2.table.style.format('{:.1%}'))

for u in analysis.universities:
    print("Die ähnlichste Drittmittelstruktur der " + u + ": ")
    display(s.similarities.most_similar_to(u).style.format({'similarity': '{:.1%}'}))
    print("Das ähnlichste Forschungsprofil der " + u + ": ")
    display(s2.similarities.most_similar_to(u).style.format({'similarity': '{:.1%}'}))

display(r.ranking.style.format({'value': '{:.1%}'}))
print("Gesamt: " + '{:,} €'.format(s.total) + "\n")
        
print(uni + " ist an " + str(r.rank_of(uni)) + ". Stelle")
print("Besser sind: ")
display(r.better_rank_than(uni).style.format({'value': '{:.1%}'}))
        
print("Drittmittelstruktur der " + uni + ":")
display(s.structure_of(uni).style.format({uni: '{:.1%}'}))
display(s.structure_of('Universität für angewandte Kunst Wien').style.format({'Universität für angewandte Kunst Wien': '{:.1%}'}))

print("Die Top-10 Universitäten sind: ")
display(r.top(10).style.format({'value': '{:.1%}'}))

class University:
    def __init__(self, name):
        self.__name = name   
        self.__analyses = dict()
        
    @property
    def name(self):
        return self.__name
        
    def add_analysis(self, analysis):
        self.__analyses[analysis.description] = analysis
        

univie = University("Universität Wien")
univie.add_analysis(analysis)










TMP for Universität für Bodenkultur Wien:


funder                                              Bund (Ministerien)  \
university                                                               
Akademie der bildenden Künste Wien                            0.062828   
Medizinische Universität Graz                                 0.015341   
Medizinische Universität Innsbruck                            0.097527   
Medizinische Universität Wien                                 0.019369   
Montanuniversität Leoben                                      0.088135   
Technische Universität Graz                                   0.019578   
Technische Universität Wien                                   0.028274   
Universität Graz                                              0.035644   
Universität Innsbruck                                         0.020646   
Universität Klagenfurt                                        0.150205   
Universität Linz                                              0.017202   
Universität Mozarteum Salzburg                                0.406862   
Universität Salzburg                                          0.073663   
Universität Wien                                              0.047600   
Universität für Bodenkultur Wien                              0.086673   
Universität für Musik und darstellende Kunst Graz             0.129834   
Universität für Musik und darstellende Kunst Wien             0.122623   
Universität für Weiterbildung Krems                           0.138891   
Universität für angewandte Kunst Wien                         0.078350   
Universität für künstlerische und industrielle ...            0.348982   
Veterinärmedizinische Universität Wien                        0.053376   
Wirtschaftsuniversität Wien                                   0.045157   

funder                                                    EU       FFG  \
university                                                               
Akademie der bildenden Künste Wien                  0.002453  0.000000   
Medizinische Universität Graz                       0.045322  0.020185   
Medizinische Universität Innsbruck                  0.083717  0.016313   
Medizinische Universität Wien                       0.096658  0.006610   
Montanuniversität Leoben                            0.096686  0.232250   
Technische Universität Graz                         0.169743  0.280631   
Technische Universität Wien                         0.190129  0.172842   
Universität Graz                                    0.125077  0.041626   
Universität Innsbruck                               0.213662  0.090954   
Universität Klagenfurt                              0.160192  0.108593   
Universität Linz                                    0.092978  0.258998   
Universität Mozarteum Salzburg                      0.000000  0.000000   
Universität Salzburg                                0.181432  0.044150   
Universität Wien                                    0.182879  0.018483   
Universität für Bodenkultur Wien                    0.191074  0.045726   
Universität für Musik und darstellende Kunst Graz   0.000000  0.031196   
Universität für Musik und darstellende Kunst Wien   0.257061  0.000000   
Universität für Weiterbildung Krems                 0.148333  0.114180   
Universität für angewandte Kunst Wien               0.215729  0.024098   
Universität für künstlerische und industrielle ...  0.000000  0.000000   
Veterinärmedizinische Universität Wien              0.067971  0.003563   
Wirtschaftsuniversität Wien                         0.241094  0.037352   

funder                                                   FWF  \
university                                                     
Akademie der bildenden Künste Wien                  0.710589   
Medizinische Universität Graz                       0.092771   
Medizinische Universität Innsbruck                  0.217386   
Medizinische Universität Wien                       0.217981   
Montanuniversität Leoben                            0.034675  

funder                                              Bund (Ministerien)  \
university                                                               
Akademie der bildenden Künste Wien                            0.724882   
Medizinische Universität Graz                                 0.176999   
Medizinische Universität Innsbruck                            1.125223   
Medizinische Universität Wien                                 0.223471   
Montanuniversität Leoben                                      1.016866   
Technische Universität Graz                                   0.225878   
Technische Universität Wien                                   0.326216   
Universität Graz                                              0.411244   
Universität Innsbruck                                         0.238201   
Universität Klagenfurt                                        1.732999   
Universität Linz                                              0.198465   
Universität Mozarteum Salzburg                                4.694201   
Universität Salzburg                                          0.849898   
Universität Wien                                              0.549194   
Universität für Bodenkultur Wien                              1.000000   
Universität für Musik und darstellende Kunst Graz             1.497976   
Universität für Musik und darstellende Kunst Wien             1.414776   
Universität für Weiterbildung Krems                           1.602462   
Universität für angewandte Kunst Wien                         0.903975   
Universität für künstlerische und industrielle ...            4.026405   
Veterinärmedizinische Universität Wien                        0.615832   
Wirtschaftsuniversität Wien                                   0.521000   

funder                                                    EU       FFG  \
university                                                               
Akademie der bildenden Künste Wien                  0.012838  0.000000   
Medizinische Universität Graz                       0.237198  0.441427   
Medizinische Universität Innsbruck                  0.438140  0.356751   
Medizinische Universität Wien                       0.505865  0.144553   
Montanuniversität Leoben                            0.506016  5.079132   
Technische Universität Graz                         0.888365  6.137177   
Technische Universität Wien                         0.995056  3.779910   
Universität Graz                                    0.654600  0.910329   
Universität Innsbruck                               1.118219  1.989094   
Universität Klagenfurt                              0.838380  2.374841   
Universität Linz                                    0.486609  5.664086   
Universität Mozarteum Salzburg                      0.000000  0.000000   
Universität Salzburg                                0.949537  0.965517   
Universität Wien                                    0.957115  0.404214   
Universität für Bodenkultur Wien                    1.000000  1.000000   
Universität für Musik und darstellende Kunst Graz   0.000000  0.682226   
Universität für Musik und darstellende Kunst Wien   1.345352  0.000000   
Universität für Weiterbildung Krems                 0.776312  2.497031   
Universität für angewandte Kunst Wien               1.129034  0.527008   
Universität für künstlerische und industrielle ...  0.000000  0.000000   
Veterinärmedizinische Universität Wien              0.355730  0.077911   
Wirtschaftsuniversität Wien                         1.261786  0.816858   

funder                                                   FWF  \
university                                                     
Akademie der bildenden Künste Wien                  3.420321   
Medizinische Universität Graz                       0.446539   
Medizinische Universität Innsbruck                  1.046359   
Medizinische Universität Wien                       1.049220   
Montanuniversität Leoben                            0.166902  

TMP for Universität Wien:


funder                                              Bund (Ministerien)  \
university                                                               
Akademie der bildenden Künste Wien                            0.062828   
Medizinische Universität Graz                                 0.015341   
Medizinische Universität Innsbruck                            0.097527   
Medizinische Universität Wien                                 0.019369   
Montanuniversität Leoben                                      0.088135   
Technische Universität Graz                                   0.019578   
Technische Universität Wien                                   0.028274   
Universität Graz                                              0.035644   
Universität Innsbruck                                         0.020646   
Universität Klagenfurt                                        0.150205   
Universität Linz                                              0.017202   
Universität Mozarteum Salzburg                                0.406862   
Universität Salzburg                                          0.073663   
Universität Wien                                              0.047600   
Universität für Bodenkultur Wien                              0.086673   
Universität für Musik und darstellende Kunst Graz             0.129834   
Universität für Musik und darstellende Kunst Wien             0.122623   
Universität für Weiterbildung Krems                           0.138891   
Universität für angewandte Kunst Wien                         0.078350   
Universität für künstlerische und industrielle ...            0.348982   
Veterinärmedizinische Universität Wien                        0.053376   
Wirtschaftsuniversität Wien                                   0.045157   

funder                                                    EU       FFG  \
university                                                               
Akademie der bildenden Künste Wien                  0.002453  0.000000   
Medizinische Universität Graz                       0.045322  0.020185   
Medizinische Universität Innsbruck                  0.083717  0.016313   
Medizinische Universität Wien                       0.096658  0.006610   
Montanuniversität Leoben                            0.096686  0.232250   
Technische Universität Graz                         0.169743  0.280631   
Technische Universität Wien                         0.190129  0.172842   
Universität Graz                                    0.125077  0.041626   
Universität Innsbruck                               0.213662  0.090954   
Universität Klagenfurt                              0.160192  0.108593   
Universität Linz                                    0.092978  0.258998   
Universität Mozarteum Salzburg                      0.000000  0.000000   
Universität Salzburg                                0.181432  0.044150   
Universität Wien                                    0.182879  0.018483   
Universität für Bodenkultur Wien                    0.191074  0.045726   
Universität für Musik und darstellende Kunst Graz   0.000000  0.031196   
Universität für Musik und darstellende Kunst Wien   0.257061  0.000000   
Universität für Weiterbildung Krems                 0.148333  0.114180   
Universität für angewandte Kunst Wien               0.215729  0.024098   
Universität für künstlerische und industrielle ...  0.000000  0.000000   
Veterinärmedizinische Universität Wien              0.067971  0.003563   
Wirtschaftsuniversität Wien                         0.241094  0.037352   

funder                                                   FWF  \
university                                                     
Akademie der bildenden Künste Wien                  0.710589   
Medizinische Universität Graz                       0.092771   
Medizinische Universität Innsbruck                  0.217386   
Medizinische Universität Wien                       0.217981   
Montanuniversität Leoben                            0.034675  

...

Die ähnlichste Drittmittelstruktur der Universität für künstlerische und industrielle Gestaltung Linz: 


Das ähnlichste Forschungsprofil der Universität für künstlerische und industrielle Gestaltung Linz: 


Gesamt: 605,400,700 €

Universität Wien ist an 3. Stelle
Besser sind: 


Drittmittelstruktur der Universität Wien:


Die Top-10 Universitäten sind: 
